In [1]:
import pandas as pd
import random
from ast import literal_eval
import gurobipy as gb
import numpy as np
import networkx as nx

In [2]:
def dateCoding(date):
    d = 0
    day = str(date)[8:10]
    if (day == '12'):
        d = 1
    h = str(date)[11:13]
    m = str(date)[14:16]
    return d*1440+int(h)*60 + int(m)

def calc_flight_cost(flight):
    dep = flight['sobt']
    arr = flight['sibt']
    dep = pd.to_datetime(str(dep))
    arr = pd.to_datetime(str(arr))
    return calc_minutes(arr-dep) * 1000/60
    
def calc_minutes(date):
    h = str(date)[7:9]
    m = str(date)[10:12]
    return int(m)+int(h)*60

def calc_route_cost(route):
    cost = 0
    for f in route:
        cost += calc_flight_cost(total_flights.iloc[nid_index_dict[f],:])
    return cost

Inizializzazione dataset voli

In [3]:
flights = pd.read_csv('/Users/simonecossaro/Downloads/flight_schedules.csv').iloc[:,1:]
bbf = flights[flights.airline=='EZY']
ef2 = bbf
ef2 = ef2.reset_index()

nid_index_dict = dict()
index_nid_dict = dict()
for i in range(len(ef2)):
    nid_index_dict[ef2.iloc[i,1]] = i
    index_nid_dict[i] = ef2.iloc[i,1]

ef2 = ef2.iloc[:,1:]

mandatory = list()
for f in range(len(ef2)):
    if (random.random() > 0.90):
        mandatory.append(0)
    else:
        mandatory.append(1)
        
ef2['mandatory'] = mandatory

nf = len(ef2)

In [4]:
flights_copies = list()
counter = 1001
for i in range(nf):
    list1 = list()
    list1.append(ef2.iloc[i,0])
    list1.append(counter)
    counter += 1
    list1.append(counter)
    counter += 1
    flights_copies.append(list1)

In [5]:
total_flights = pd.DataFrame(columns=ef2.columns)
for i in range(nf):
    total_flights = total_flights.append(ef2.iloc[i,:])
counter = 1001
for i in range(nf):
    x = ef2.iloc[i,:]
    x['nid']= counter
    counter += 1
    x['sobt']= pd.to_datetime(x['sobt'])+pd.Timedelta(10,'m')
    x['sibt']= pd.to_datetime(x['sibt'])+pd.Timedelta(10,'m')
    total_flights = total_flights.append(x)
    y = ef2.iloc[i,:]
    y['nid']= counter
    counter += 1
    y['sobt']= pd.to_datetime(y['sobt'])-pd.Timedelta(10,'m')
    y['sibt']= pd.to_datetime(y['sibt'])-pd.Timedelta(10,'m')
    total_flights = total_flights.append(y)

total_flights = total_flights.reset_index()
total_flights = total_flights.iloc[:,1:]

/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use panda

/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use panda

/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use panda

/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use panda

/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(ef2.iloc[i,:])
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use panda

...

/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  x['nid']= counter
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  x['sobt']= pd.to_datetime(x['sobt'])+pd.Timedelta(10,'m')
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-vi

/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  x['nid']= counter
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  x['sobt']= pd.to_datetime(x['sobt'])+pd.Timedelta(10,'m')
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-vi

/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  y['nid']= counter
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  y['sobt']= pd.to_datetime(y['sobt'])-pd.Timedelta(10,'m')
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-

/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:11: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_flights = total_flights.append(x)
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  y['nid']= counter
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  y['sobt']= pd.to_datetime(y['sobt'])-pd.Timedelta(10,'m')
/var/folders/hp/tc43d6dx38xf9lzc4x4y5

/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  x['nid']= counter
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  x['sobt']= pd.to_datetime(x['sobt'])+pd.Timedelta(10,'m')
/var/folders/hp/tc43d6dx38xf9lzc4x4y5l0m0000gn/T/ipykernel_1612/1405286204.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-vi

In [6]:
nid_index_dict = dict()
index_nid_dict = dict()
for i in range(len(total_flights)):
    nid_index_dict[total_flights.iloc[i,0]] = i
    index_nid_dict[i] = total_flights.iloc[i,0]

Creazione itinerari

In [7]:
G = nx.MultiDiGraph()
airports = ef2['origin'].unique()
G.add_nodes_from(airports)
for f in range(len(ef2)):
    G.add_edge(ef2.iloc[f,7],ef2.iloc[f,8],flight=ef2.iloc[f,0])
    
it = list()
for n1 in G.nodes():
    for n2 in G.neighbors(n1):
        it.append([n1,n2])
n_dir = len(it)

for n1 in G.nodes():
    for n2 in G.neighbors(n1):
        for n3 in G.neighbors(n2):
            for e1 in range(len(G[n1][n2])):
                for e2 in range(len(G[n2][n3])):
                    if ((n1!=n3) and pd.to_datetime(ef2.iloc[nid_index_dict[G[n2][n3][e2]['flight']],11])-pd.to_datetime(ef2.iloc[nid_index_dict[G[n1][n2][e1]['flight']],12]) > pd.Timedelta(30, "m")
                       and pd.to_datetime(ef2.iloc[nid_index_dict[G[n2][n3][e2]['flight']],11])-pd.to_datetime(ef2.iloc[nid_index_dict[G[n1][n2][e1]['flight']],12]) < pd.Timedelta(3, "h")):
                        if (not([n1,n2,n3] in it)):
                            it.append([n1,n2,n3])

n_it = len(it)
n_os = n_it-n_dir

In [8]:
def find_flights_itineraries(itinerary):
    list1 = list()
    flights1 = ef2[ef2['origin']== itinerary[0]]
    flight1 = flights1[flights1['destination']== itinerary[1]].iloc[0,0]
    list1.append(flight1)
    flights2 = ef2[ef2['origin']== itinerary[1]]
    flights2 = flights2[flights2['destination']== itinerary[2]]
    for f in range(len(flights2)):
        if (pd.to_datetime(flights2.iloc[f,11])-pd.to_datetime(ef2.iloc[nid_index_dict[flight1],12]) > pd.Timedelta(30, "m")):
            flight2 = flights2.iloc[f,0]
            list1.append(flight2)
            return list1

In [9]:
direct_itineraries = list()
one_stop_itineraries = list()
for i in it:
    if (len(i)==2):
        direct_itineraries.append(i)
    elif(len(i)==3):
        one_stop_itineraries.append(i)
        
flights_itineraries = list()
for i in direct_itineraries:
    flights = ef2[ef2['origin']== i[0]]
    flight = flights[flights['destination']== i[1]].iloc[0,0]
    list1 = list()
    list1.append(flight)
    flights_itineraries.append(list1)
for i in one_stop_itineraries:
    flights_itineraries.append(find_flights_itineraries(i))

In [10]:
I = list()
for i in it:
    I.append(i)
    
FI = list()
for i in flights_itineraries:
    FI.append(i)

for i in range(n_dir):
    I.append(it[i])
    l = list()
    l.append(flights_copies[nid_index_dict[FI[i][0]]][1])
    FI.append(l)

for i in range(n_dir):
    I.append(it[i])
    l = list()
    l.append(flights_copies[nid_index_dict[FI[i][0]]][2])
    FI.append(l)
    
for i in range(n_dir,n_it):
    for p1 in flights_copies[nid_index_dict[FI[i][0]]]:
        for p2 in flights_copies[nid_index_dict[FI[i][1]]]:
            if (p1!= FI[i][0] or p2!= FI[i][1]):
                I.append(it[i])
                list1 = list()
                list1.append(p1)
                list1.append(p2)
                FI.append(list1)

AIRCRAFT ROUTES

In [11]:
f_list = list(ef2['nid'])
G2 = nx.Graph()
G2.add_nodes_from(ef2['nid'])
for i in range(len(ef2)):
    if (pd.notnull(ef2.iloc[i,21]) and (ef2.iloc[i,21] in f_list)):
        G2.add_edge(ef2.iloc[i,21], ef2.iloc[i,0])
        
aircraft_routes = list()
for i in nx.connected_components(G2):
    aircraft_routes.append(i)

In [12]:
A = list()
for i in range(1,len(aircraft_routes)+1):
    if (i<10):
        s = "00" + str(i)
    if (i>= 10 and i<100):
        s = "0" + str(i)
    if (i>=100):
        s = str(i)
    A.append("IBB"+s)
    
ef2['aircraft_id'] = 0
for i in range(len(aircraft_routes)):
    for j in aircraft_routes[i]:
        ef2.loc[ef2['nid']== j,'aircraft_id'] = A[i]

In [13]:
def substitution_in_list(r,f,p):
    index = len(r)+1
    for i in range(len(r)):
        if (r[i] == f):
            index = i
            break
    r[index] = p
    return r

In [14]:
RAR = list()
for r in aircraft_routes:
    list1 = list()
    list1.append(list(r))
    for f in r:
        for p in flights_copies[nid_index_dict[f]]:
            list2 = list(r)
            list2 = substitution_in_list(list2,f,p)
            if (list2 != list(r)):
                list1.append(list2)
    RAR.append(list1)          

RA = list()
ci = 0
for i in range(len(RAR)):
    list1 = list()
    for j in range(len(RAR[i])):
        list1.append(ci)
        ci+=1
    RA.append(list1)
    
R = list()
for i in range(len(RAR)):
    for j in range(len(RAR[i])):
        R.append(RAR[i][j])

In [15]:
aircraft_types = ef2['aircraft_type'].unique()
aircraft_clusters = pd.read_csv('/Users/simonecossaro/Downloads/aircraftClustering.csv')
cluster_seat = pd.read_csv('/Users/simonecossaro/Downloads/aircraftSeats.csv')

In [16]:
aircrafts = pd.DataFrame(A, columns =['aircraft_ID'])

In [17]:
def getAircraftType(aircraft):
    return ef2[ef2['aircraft_id']==aircraft].iloc[0,13]

def get_number_seats(aircraft):
    aircraft_cluster = aircraft_clusters[aircraft_clusters['AircraftType']==aircraft]['AssignedAircraftType'].iloc[0]
    seats = cluster_seat[cluster_seat['Aircraft']==str(aircraft_cluster)].iloc[0,2]
    return seats

In [18]:
aircraft_types = list()
for a in A:
    aircraft_types.append(getAircraftType(a))
aircrafts['type'] = aircraft_types


aircraft_seats = list()
for t in aircrafts['type']:
    aircraft_seats.append(get_number_seats(t))
aircrafts['seats'] = aircraft_seats

**SETS**

In [19]:
#I
F = total_flights.iloc[:,0]
#A
#IC
FM = total_flights[total_flights.mandatory == 1].iloc[:,0]
FO = total_flights[total_flights.mandatory == 0].iloc[:,0]
#IR
#FI
#FIO
#R
P = list()
for i in range(3):
    for f in flights_copies:
        P.append(f)

In [20]:
IC = list()
for i in FI:
    if (len(i)==2):
        IC.append(i)
        
IC_it = list()
for i in I:
    if (len(i)==3):
        IC_it.append(i)
        
IC_N_it = list()
for i in range(len(I)):
    if (len(I[i])==3):
        IC_N_it.append(i)

In [24]:
def canBeRedirect(i, j):
    dest = I[i][-1]
    if (any((I[i][a] in I[j])and(dest in I[j])and(I[j].index(I[i][a])<I[j].index(dest))for a in range(len(I[i])-1))):
        return True
    return False    

IR = list()
for i in range(len(I)):
    list1 = list()
    for j in range(len(I)):
            if (i!=j and canBeRedirect(i,j)):
                list1.append(j)
    IR.append(list1)

KeyboardInterrupt: 

In [ ]:
FIO = list()
for i in range(len(FI)):
    list1 = list()
    for f in FI[i]:
        if(total_flights.iloc[nid_index_dict[f],23] == 0):
            list1.append(f)
    FIO.append(list1)

**PARAMETERS**

In [ ]:
#D[i] the demand forecast for passenger itinerary i.
#DI[i] the maximum number of passengers carried in itinerary i.
#c[r] the operation and delay penalty cost of executing aircraft route r.
#Capa the number of seats (capacity) in aircraft a.
Cap = aircrafts.iloc[:,2]
#Fare the average fare for itinerary i.
#STDf the schedule time of departure of flight f
STD = total_flights['sobt']
#MPT the minimum passenger connection time
MPT = 30
#MTT the minimum turnaround time.
MTT = 30
#FTf the block time of flight f.
#EPDr,f the expected propagated delays of flight f in route r.
#Mf1,f2 the minimum possible connection time between flight f1, f2.
M = 30
#bij Recapture rate from itinerary i to itinerary j, bi = 1.
#devr,f deviation from the STD of flight f in aircraft route r.
#θ1 1 if flight f, copy p ∈ P is served in route r, and 0 otherwise. r,f,p f
#θ2 1 if itinerary i involves flight f, and 0 otherwise. i,f
#θ3 1 if the component flights of connecting itinerary i are executed by the same aircraft in route r, and 0 otherwise. r,i 
#γi 1 if itinerary i ∈ IC exists between flight f1, copy p1 and flight f2, copy p2. f1 p1,f2 p2

In [ ]:
def existICbetween(f1,p1,f2,p2):
    for i in IC:
        if (((i[0] == f1)or(i[0]==p1)) and ((i[1] == f2)or(i[1] == p2))):
            return True
    return False

def fare_for_flight(flight_id):
    flight = total_flights[total_flights['nid']==flight_id].iloc[0,:]
    return flight['gcdistance'] / 5
    

def fare_for_itinerary(itinerary):
    fare = 0
    for f in itinerary:
        fare += fare_for_flight(f)
    return fare

def find_min_cap(itinerary):
    minimum = np.Inf
    for i in itinerary:
        cap = total_flights[total_flights['nid']==i].iloc[0,17]
        if (cap < minimum ):
            minimum = cap
    return minimum

def find_min_pax(itinerary):
    minimum = np.Inf
    for i in itinerary:
        pax = total_flights[total_flights['nid']==i].iloc[0,18]
        if (pax < minimum ):
            minimum = pax
    return minimum

In [ ]:
D = list()
for i in range(len(FI)):
    D.append(find_min_pax(FI[i]))

DI = list()
for i in range(len(FI)):
    DI.append(find_min_cap(FI[i]))
    
c = list()
for i in range(len(R)):
    c.append(calc_route_cost(R[i]))
    
Fare = list()
for i in FI:
    Fare.append(fare_for_itinerary(i))
    
FT = list()
for i in range(len(F)):
    dep = pd.to_datetime(total_flights['sobt']).iloc[i]
    arr = pd.to_datetime(total_flights['sibt']).iloc[i]
    time = arr - dep
    FT.append(calc_minutes(time))

dev = list()
for r in range(len(R)):
    list1 = list()
    for f in range(len(F)):
        if (P[f][0] in R[r]):
            list1.append(random.randint(1,10))
        else:
            list1.append(0)
    dev.append(list1)
             
EPD = list()
for r in range(len(R)):
    list1 = list()
    for f in range(len(R[r])):
        delay_sum = 0
        for d in range(f):
            delay_sum += dev[r][f]
        list1.append(delay_sum)
    EPD.append(list1)
             
             
B2 = list()
for i in range(len(I)):
    list1 = list()
    rate_max = 0.4
    for j in range(len(I)):
        if (not(j in IR[i])):
            list1.append(0)
        else:
            r = random.randint(0,5)/100
            if (rate_max > r):
                list1.append(r)
                rate_max -= r
            else:
                list1.append(rate_max)
                rate_max = 0
    B2.append(list1)

Θ1 = list()
for i in range(len(total_flights)):
    list1 = list()
    for p in P[i]:
        list2 = list()
        for j in range(len(R)):
            if (p in R[j]):
                list2.append(1)
            else:
                list2.append(0)
        list1.append(list2)
    Θ1.append(list1)
    
Θ2 = list()
for i in FI:
    list1 = np.zeros(len(total_flights))
    for f in i:
        list1[nid_index_dict[f]] = 1
    Θ2.append(list1)

Θ3 = list()
for i in FI:
    list1 = list()
    for j in range(len(R)):
        if (all(flight in R[j] for flight in i)):
            list1.append(1)
        else:
            list1.append(0)
    Θ3.append(list1)

γ = list()
for i in FI:
    list1 = list()
    for f1 in i:
        list2 = list()
        for p1 in P[nid_index_dict[f1]]:
            list3 = list()
            for f2 in i:
                list4 = list()
                for p2 in P[nid_index_dict[f2]]:
                    if (f1 == f2 or existICbetween(f1,p1,f2,p2)):
                        list4.append(1)
                    else:
                        list4.append(0)
                list3.append(list4)
            list2.append(list3)
        list1.append(list2)        
    γ.append(list1)

**MODEL 1**

In [ ]:
model1 = gb.Model()
model1.modelSense = gb.GRB.MAXIMIZE

# DECISION VARIABLES
# x_a,r : 1 if aircraft a flies route r, and 0 otherwise
X = model1.addVars( [(a,r) for a in range(len(A)) for r in range(len(RA[a]))], vtype=gb.GRB.BINARY)
# y_f,p : 1 if flight copy p of flight f is selected, and 0 otherwise
Y = model1.addVars( [(f,p) for f in range(len(F)) for p in range(len(P[f]))], vtype=gb.GRB.BINARY)
# w_f1p1,f2p2 : 1 if flight copy pair (f1p1,f2,p2)is selected, 0 otherwise
W = model1.addVars( [(f1,p1,f2,p2) for f1 in range(len(F)) for p1 in range(len(P[f1])) 
                         for f2 in range(len(F)) for p2 in range(len(P[f2]))], vtype=gb.GRB.BINARY)
# h_i : the number of passengers travelling in itinerary i
H = model1.addVars([i for i in range(len(I))], vtype=gb.GRB.INTEGER, lb = 0)

In [ ]:
# (1) OBJECTIVE FUNCTION
model1.setObjective( 
     ((gb.quicksum( (Fare[i]*H[i]) for i in range(len(I)) )) - (gb.quicksum((gb.quicksum((c[r]*X[a,r])for r in range(len(RA[a])))for a in range(len(A)) ) )  )))
# CONSTRAINTS
# (2) ensure that every flight is assigned to an aircraft
for f in range(len(F)):
    for p in range(len(P[f])):
        model1.addConstr(gb.quicksum((gb.quicksum(Θ1[f][p][RA[a][r]]*X[a,r] for r in range(len(RA[a])))) for a in range(len(A)) ) == Y[f,p] )
# (3) ensure that exactly one flight copy will be selected for each flight
for f in range(len(F)):
    model1.addConstr( gb.quicksum(Y[f,p] for p in range(len(P[f]))) == 1 )
# (4) ensure that every aircraft takes at most one route
for a in range(len(A)):
    model1.addConstr( gb.quicksum(X[a,r] for r in range(len(RA[a]))) <= 1 )
# (5) limit the number of passengers taken on itineraries to the forecast demand 
for i in range(len(I)):
    model1.addConstr( H[i] <= D[i] )
# (6) limit the number of passengers taken on itineraries to the number of available aircraft seats
for f in range(len(F)):
    model1.addConstr( gb.quicksum((Θ2[i][f]*H[i]) for i in range(len(I))) <= 
                         gb.quicksum((Cap[a] * gb.quicksum((gb.quicksum((Θ1[f][p][RA[a][r]]*X[a,r])for p in range(len(P[f]))))for r in range(len(RA[a]))))for a in range(len(A)) ))  
#(11)
for i in range(len(FI)):
    for fm in FI[i]:
        for fn in FI[i]:
            if(Θ2[i][nid_index_dict[fm]] == 1 and Θ2[i][nid_index_dict[fn]] == 1):
                model1.addConstr( H[i] <= D[i]*gb.quicksum((gb.quicksum(γ[i][FI[i].index(fm)][pm][FI[i].index(fn)][pn]*W[nid_index_dict[fm],pm,nid_index_dict[fn],pn] for pn in range(len(P[nid_index_dict[fn]])))for pm in range(len(P[nid_index_dict[fm]]))) ))
#(12)
for i in range(len(I)):
    for fm in range(len(FI[i])):
        for fn in range(len(FI[i])):
            for pm in range(len(P[fm])):
                for pn in range(len(P[fn])):
                    model1.addConstr( W[fm,pm,fn,pn] <= Y[fm,pm] )
#(13)
for i in range(len(I)):
    for fm in range(len(FI[i])):
        for fn in range(len(FI[i])):
            for pm in range(len(P[fm])):
                for pn in range(len(P[fn])):
                    model1.addConstr( W[fm,pm,fn,pn] <= Y[fn,pn] )
#(14)
for i in range(len(I)):
    for fm in range(len(FI[i])):
        for fn in range(len(FI[i])):
            for pm in range(len(P[fm])):
                for pn in range(len(P[fn])):
                    model1.addConstr( W[fm,pm,fn,pn] >= Y[fm,pm]+Y[fn,pn]-1 )

In [ ]:
model1.optimize()

**MODEL 2**

In [ ]:
model22 = gb.Model()
model22.modelSense = gb.GRB.MAXIMIZE

# DECISION VARIABLES
# x_a,r : 1 if aircraft a flies route r, and 0 otherwise
X = model22.addVars( [(a,r) for a in range(len(A)) for r in range(len(RA[a]))], vtype=gb.GRB.BINARY)
# y_f,p : 1 if flight copy p of flight f is selected, and 0 otherwise
Y = model22.addVars( [(f,p) for f in range(len(F)) for p in range(len(P[f]))], vtype=gb.GRB.BINARY)
# z_i : 1 if itinerary i is selected for inclusion, and 0 otherwise
Z = model22.addVars([i for i in range(len(I))], vtype=gb.GRB.BINARY)
# h_i : the number of passengers travelling in itinerary i
H = model22.addVars([i for i in range(len(I))], vtype=gb.GRB.INTEGER, lb = 0)
# t_i,j : the number of passengers requesting itinerary i that the airline attempts to redirect to itinerary j
T = model22.addVars( [(i,j) for i in range(len(I)) for j in range(len(I))], vtype=gb.GRB.INTEGER, lb = 0)
# edt_f : the expected departure time of flight f under expected propagated delays
EDT = model22.addVars([f for f in range(len(F))], vtype=gb.GRB.INTEGER, lb = 0)
# tf_i : 1 if the two connecting flights of itinerary i are operated by the same aircraft (i.e. through flight), and 0 otherwise
TF = model22.addVars([i for i in range(len(IC))], vtype=gb.GRB.BINARY)

In [ ]:
# (1) OBJECTIVE FUNCTION
model22.setObjective( 
     ((gb.quicksum( (Fare[i]*H[i]) for i in range(len(I)) )) - (gb.quicksum((gb.quicksum((c[r]*X[a,r])for r in range(len(RA[a])))for a in range(len(A)) ) )  )))
# CONSTRAINTS
# (2) ensure that every flight is assigned to an aircraft
for f in range(len(F)):
    for p in range(len(P[f])):
        model22.addConstr(gb.quicksum((gb.quicksum(Θ1[f][p][RA[a][r]]*X[a,r] for r in range(len(RA[a])))) for a in range(len(A)) ) == Y[f,p] )
# (4) ensure that every aircraft takes at most one route
for a in range(len(A)):
    model22.addConstr( gb.quicksum(X[a,r] for r in range(len(RA[a]))) <= 1 )
# (17)
for f in FM:
    model22.addConstr(gb.quicksum(Y[nid_index_dict[f],p] for p in range(len(P[nid_index_dict[f]]))) == 1)
# (18)
for f in FO:
    model22.addConstr(gb.quicksum(Y[nid_index_dict[f],p] for p in range(len(P[nid_index_dict[f]]))) <= 1)
# (19)
for f in range(len(F)):
    model22.addConstr(EDT[f] == dateCoding(STD[f]) + 
                         gb.quicksum((gb.quicksum((dev[r][f]*X[a,r])for r in range(len(RA[a]))))for a in range(len(A)))
                        )               
# (20)
for i in range(len(I)):
    model22.addConstr( H[i] <= D[i] - gb.quicksum(((T[i,j]-B2[i][j]*T[j,i]))for j in IR[i]) )   
# (myConstr)
for i in range(len(I)):
    for j in range(len(I)):
        if (not(j in IR[i])):
            model22.addConstr( T[i,j] == 0 )            
# (21)
for i in range(len(I)):
    for f in FIO[i]:
        model22.addConstr( Z[i] <= gb.quicksum((Y[nid_index_dict[f],p])for p in range(len(P[nid_index_dict[f]]))))
# (22)
for i in range(len(IC)):
    model22.addConstr(TF[i] == gb.quicksum((gb.quicksum((Θ3[i][RA[a][r]]*X[a,r])for r in range(len(RA[a]))))for a in range(len(A))))
# (23)
for i in range(len(IC)):
    f1 = nid_index_dict[IC[i][0]]
    f2 = nid_index_dict[IC[i][1]]
    model22.addConstr( EDT[f2] - EDT[f1] - FT[f1] >= 
                                 (-MPT + MTT)* TF[i] + MPT*Z[IC_N_it[i]] - M*(1-Z[IC_N_it[i]]) )
# (24)
for f in range(len(F)):
    model22.addConstr( gb.quicksum((Θ2[i][f]*H[i]) for i in range(len(I))) <= 
                           gb.quicksum((Cap[a] * gb.quicksum((gb.quicksum((Θ1[f][p][RA[a][r]]*X[a,r])for p in range(len(P[f]))))for r in range(len(RA[a]))))for a in range(len(A)) ))                        
# (25)
for i in range(len(I)):
    model22.addConstr( H[i] <= DI[i]*Z[i] )
# (30)
for i in range(len(I)):
    for j in range(len(IR[i])):
        model22.addConstr( T[i,j] <= D[i] )

In [ ]:
model22.optimize()

**VNS**

In [ ]:
class VNS:
    def __init__(self, initial_solution, neighborhood_func):
        self.current_solution = initial_solution
        self.neighborhood_func = neighborhood_func
        
    def search(self, P1, N):
        S1,obj1 = evaluator2(P1)
        k = 1
        while (k <= N):
            neighbors = neighborhood(P1,10)
            P2 = random.choice(neighbors)
            if (P2!=None):
                S2,obj2 = evaluator2(P2)
            else:
                obj2 = 0
            if (obj1 >= obj2):
                k += 1
            else:
                obj1,P1 = obj2,P2
        return S1,obj1

In [ ]:
def neighborhood(solution,M):
    neighbors = []
    for i in range(M):
        neighbors.append(cross(solution,len(P)))
        neighbors.append(insert(solution,len(P)))
        neighbors.append(swap(solution,len(P)))
        neighbors.append(delete(solution,len(P)))
    return neighbors
                    
def cross(P,K):
    k = 1
    while (k<=K):
        n1 = random.randint(0,len(P)-1)
        p1 = P[n1]
        for n2 in range(len(P)):
            if (n1 != n2):
                for u in range(1,len(P[n1])):
                    for v in range(1,len(P[n2])):
                        if (con(P[n1][u-1],P[n2][v]) and con(P[n2][v-1],P[n1][u])):
                            P2 = P
                            P2[n1][u] = P[n2][v]
                            P2[n2][v] = P[n1][u]
                            return P2
        k +=1

def insert(P,K):
    k = 1
    while (k<=K):
        n1 = random.randint(0,len(P)-1)
        p1 = P[n1]
        for n2 in range(len(P)):
            if (n1 != n2):
                for u in range(1,len(P[n1])):
                    for v in range(1,len(P[n2])):
                        for w in range(0,len(P[n2])-1):
                            if (v!=w and con(P[n1][u-1],P[n2][v]) and con(P[n2][w],P[n1][u]) 
                                and arr(P[n2][v-1])==dep(P[n2][w+1])):
                                P2 = P
                                x = P[n2][v:w+1]
                                for i in range(len(x)):
                                    P2[n2].remove(x[i])
                                for i in range(len(x)):
                                    P2[n1].insert(u+i,x[i])
                                return P2
        k +=1

        
def swap(P,K):
    k = 1
    while (k<=K):
        n1 = random.randint(0,len(P)-1)
        p1 = P[n1]
        for n2 in range(len(P)):
            if (n1 != n2):
                for u in range(1,len(P[n1])-1):
                    for v in range(1,len(P[n2])-1):
                        if (con(P[n1][u-1],P[n2][v]) and con(P[n2][v],P[n1][u+1]) and con(P[n2][v-1],P[n1][u]) 
                            and con(P[n1][u],P[n2][v+1])):
                            P2 = P
                            P2[n1][u] = P[n2][v]
                            P2[n2][v] = P[n1][u]
                            return P2
        k +=1
                            

def delete(P,K):
    k = 1
    while (k<=K):
        n1 = random.randint(0,len(P)-1)
        p1 = P[n1]
        for u in range(len(P[n1])):
            if (isOptional(P[n1][u])):
                for n2 in range(len(P)):
                    if (n1 != n2):
                        for v1 in range(len(P[n2])-1):
                            if (dep(P[n1][u])==dep(P[n2][v1])):
                                for v2 in range(v1,len(P[n2])):
                                    if (arr(P[n1][u])==dep(P[n2][v2])):
                                        P2 = P
                                        P2[n1].remove(P[n1][u])
                                        for i in range(v1,v2+1):
                                            P2[n1].insert(u+(i-v1),P[n2][i])
                                        return P2
        k +=1
            

def dep(f):
    return total_flights[total_flights.nid == f].iloc[0,7]

def arr(f):
    return total_flights[total_flights.nid == f].iloc[0,8]

def con(f1,f2):
    if (arr(f1)==dep(f2)):
        return True
    return False

def isOptional(f):
    if (total_flights[total_flights.nid == f].iloc[0,23] == 0):
        return True
    return False

In [ ]:
lr = list()
for i in range(len(RAR)):
    list1 = list()
    for j in range(len(RAR[i][0])):
        list1.append(RAR[i][0][j])
    lr.append(list1)

In [ ]:
def flight_to_direct_itinerary(flight,itineraries):
    flight_origin = total_flights[total_flights.nid == flight].iloc[0,7]
    flight_dest = total_flights[total_flights.nid == flight].iloc[0,8]
    for i in range(len(I)):
        if (len(I[i]) == 2 and I[i][0] == flight_origin and I[i][1] == flight_dest and (i in itineraries)):
            return i
        
def calc_max_fare_ij(itinerary,itineraries,fare,B22):
    max_fare = 0
    j_max = 0
    for j in range(len(itineraries)):
        obj = fare[j]*B22[int(itinerary)][j] - fare[int(itinerary)]
        if(obj > max_fare):
            max_fare = obj
            j_max = j
    return max_fare, j_max

In [ ]:
def evaluator2(P):
    flights_selected = list()
    for r in P:
        for f in r:
            if (not(f in flights_selected)):
                flights_selected.append(f)
                
    itineraries_selected = list()
    for i in range(len(FI)):
        if (all(f in flights_selected for f in FI[i])):
            itineraries_selected.append(i)
    
    f_i_ev2_dict = dict()
    i_f_ev2_dict = dict()
    c = 0
    for f in flights_selected:
        f_i_ev2_dict[f] = c
        i_f_ev2_dict[c] = f
        c +=1
    
    fare = list()
    for i in itineraries_selected:
        fare.append(Fare[i])
        
    dit = pd.DataFrame(columns=['n_dit','fare_d'])
    osit = pd.DataFrame(columns=['n_osit','fare_os'])
    for i in range(len(fare)):
        if (len(FI[itineraries_selected[i]])==1):
            dit.loc[len(dit)]= [i,fare[i]]
        elif(len(FI[itineraries_selected[i]])==2):
            osit.loc[len(osit)]= [i,fare[i]]
    dit_ord = dit.sort_values('fare_d',ascending=False)
    osit_ord = osit.sort_values('fare_os',ascending=False)
    
    B22 = list()
    for i in itineraries_selected:
        list1 = list()
        for j in itineraries_selected:
            list1.append(B2[i][j])
        B22.append(list1)
        
    di = list()
    for i in itineraries_selected:
        di.append(DI[i])
    
    H = np.zeros(len(itineraries_selected))
    remain = list()
    for f in flights_selected:
        remain.append(get_number_seats(total_flights[total_flights.nid ==f].iloc[0,13]))
    
    #step1
    for i in range(len(dit_ord)):
        flow = min(di[int(dit_ord.iloc[i,0])],remain[f_i_ev2_dict[FI[itineraries_selected[int(dit_ord.iloc[i,0])]][0]]])
        H[int(dit_ord.iloc[i,0])] = flow
        remain[f_i_ev2_dict[FI[itineraries_selected[int(dit_ord.iloc[i,0])]][0]]] -= flow
    #step2
    for i in range(len(osit_ord)):
        f1 = FI[itineraries_selected[int(osit_ord.iloc[i,0])]][0]
        f2 = FI[itineraries_selected[int(osit_ord.iloc[i,0])]][1]
        i1 = flight_to_direct_itinerary(f1,itineraries_selected)
        i2 = flight_to_direct_itinerary(f2,itineraries_selected)
        farei = fare[int(osit_ord.iloc[i,0])]
        if (i1!= None and i2!=None):
            fare1 = fare[i1]
            fare2 = fare[i2]
            if (fare1 >= fare2):
                fj = f1
                fk = f2
                j = i1
                k = i2
                farej = fare1
                farek = fare2
            else:
                fj = f2
                fk = f1
                j = i2
                k = i1
                farej = fare2
                farek = fare1
            if ( farei >= farej + farek):
                H[int(osit_ord.iloc[i,0])] = min(remain[f_i_ev2_dict[fj]]+H[j], remain[f_i_ev2_dict[fk]]+H[k], di[int(osit_ord.iloc[i,0])])
            elif( farei <= farej):
                H[int(osit_ord.iloc[i,0])] = min(remain[f_i_ev2_dict[fj]],di[int(osit_ord.iloc[i,0])])
            else:
                H[int(osit_ord.iloc[i,0])] = min(remain[f_i_ev2_dict[fk]], remain[f_i_ev2_dict[fj]]+H[j], remain[f_i_ev2_dict[fk]]+H[k],di[int(osit_ord.iloc[i,0])])
            if (H[int(osit_ord.iloc[i,0])] > H[j]):
                remain[f_i_ev2_dict[fj]] -= (H[int(osit_ord.iloc[i,0])] - H[j])
            if (H[int(osit_ord.iloc[i,0])] > H[k]):
                remain[f_i_ev2_dict[fk]] -= (H[int(osit_ord.iloc[i,0])] - H[k])
    #step3
    osit_maxfareij = pd.DataFrame(columns=['n_osit','max_fare_os','j_max_os'])
    for i in range(len(osit)):
        max_fare, j_max = calc_max_fare_ij(osit.iloc[i,0],itineraries_selected,fare,B22)
        osit_maxfareij.loc[i] = [osit.iloc[i,0],max_fare,j_max]
    osit_max_fare_ij_ord = osit_maxfareij.sort_values('max_fare_os',ascending=False)
    for i in range(len(osit_max_fare_ij_ord)):
        if (osit_max_fare_ij_ord.iloc[i,1] > 0):
            fj = FI[itineraries_selected[int(osit_ord.iloc[i,0])]][0]
            fk = FI[itineraries_selected[int(osit_ord.iloc[i,0])]][1]
            j = flight_to_direct_itinerary(fj,itineraries_selected)
            k = flight_to_direct_itinerary(fk,itineraries_selected)
            flow = min(remain[f_i_ev2_dict[fj]]+H[j], remain[f_i_ev2_dict[fk]]+H[k], di[int(osit_ord.iloc[i,2])])
            H[osit_ord.iloc[i,2]] += flow
            H[int(osit_ord.iloc[i,0])] -= flow
        else:
            H[int(osit_ord.iloc[i,0])] = di[int(osit_ord.iloc[i,0])]
    #step4
    dit_maxfareij = pd.DataFrame(columns=['n_dit','max_fare_d','j_max_d'])
    for i in range(len(dit)):
        max_fare, j_max = calc_max_fare_ij(dit.iloc[i,0],itineraries_selected,fare,B22)
        dit_maxfareij.loc[i] = [dit.iloc[i,0],max_fare,j_max]
    dit_max_fare_ij_ord = dit_maxfareij.sort_values('max_fare_d',ascending=False)
    for i in range(len(dit_max_fare_ij_ord)):
        if (dit_max_fare_ij_ord.iloc[i,1] > 0):
            fj = FI[itineraries_selected[int(dit_ord.iloc[i,0])]][0]
            fk = FI[itineraries_selected[int(dit_ord.iloc[i,0])]][1]
            j = flight_to_direct_itinerary(fj,itineraries_selected)
            k = flight_to_direct_itinerary(fk,itineraries_selected)
            flow = min(remain[f_i_ev2_dict[fj]]+H[j], remain[f_i_ev2_dict[fk]]+H[k], di[int(dit_ord.iloc[i,2])])
            H[dit_ord.iloc[i,2]] += flow
            H[int(dit_ord.iloc[i,0])] -= flow
        else:
            H[int(dit_ord.iloc[i,0])] = di[int(dit_ord.iloc[i,0])]
    #revenue calculation
    return P,gb.quicksum( fare[i]*H[i] for i in range(len(fare))).getValue()

In [ ]:
solver = VNS(lr,neighborhood)
S,o = solver.search(lr,10)
print('Aircraft routing solution: ')
print(S)
print('Revenue :'+str(o))